# การส่งข้อมูลดิจิทัลด้วยสัญญาณแบบแอนะล็อก

ช่องสัญญาณบางอย่างมีการจำกัดความถี่ต่ำสุดและสูงสุดที่ยอมให้สัญญาณผ่านไปได้ เช่นสายโทรศัพท์ยอมให้สัญญาณเสียงผ่านในช่วง 300-3000 Hz ส่วนช่องสัญญาณสำหรับใช้งานแลนไร้สายมาตรฐานหนึ่งยอมให้สัญญาณวิทยุผ่านในช่วง 2400-2500 MHz เป็นต้น

ในกรณีนี้การส่งข้อมูลโดยใช้สัญญาณแบบดิจิทัล (ซึ่งเรียกว่า baseband transmission) ไม่สามารถทำได้เนื่องจากพลังงานของสัญญาณส่วนใหญ่กระจายตัวอยู่ในบริเวณย่านความถี่ต่ำ จึงต้องมีกระบวนการโยกย้ายความถี่ของสัญญาณให้ไปอยู่ในย่ายที่ต้องการ ซึ่งเรียกว่ากระบวนการมอดูเลชัน (modulation)

## วัตถุประสงค์
* เข้าใจถึงข้อจำกัดของการส่งสัญญาณแบบดิจิทัล (baseband tranmission) ผ่านช่องสัญญาณที่มีการจำกัดความถี่ต่ำสุดและสูงสุด (bandpass channel) 
* รู้จักกระบวนการทำมอดูเลชันแบบต่าง ๆ รวมถึงความต้องการการใช้แบนด์วิธด์ที่แตกต่างกัน
* เข้าใจความหมายของ constellation diagram รวมถึงความสัมพันธ์ระหว่าง bit rate และ baud rate

## การเตรียมตัว
รันคำสั่งในเซลล์ต่อไปนี้เพื่อโหลดไลบรารีและตั้งค่าอื่น ๆ ที่ใช้งานเหมือนที่ผ่านมา

In [1]:
from sigproc import Signal, start_notebook, DEFAULT_PLOT_SETTINGS
from numpy import sin,cos,pi
from sigproc.digital import create_linecoder

bkp = start_notebook()

# ตั้งค่าให้กราฟเตี้ยลง
DEFAULT_PLOT_SETTINGS["time_fig_options"]["height"] = 200
DEFAULT_PLOT_SETTINGS["freq_fig_options"]["height"] = 200
DEFAULT_PLOT_SETTINGS["time_freq_fig_options"]["height"] = 200

/usr/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/usr/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


Loading BokehJS ...

Notebook session ready.


## กำหนดค่าตัวแปรที่ใช้ร่วมกัน
เซลล์ด้านล่างนิยามตัวแปรเอาไว้ใช้ในการสร้างกลไกมอดูเลชันและข้อมูลที่จะนำมาสร้างเป็นสัญญาณ กลับมาแก้ไขและรันเซลล์นี้ใหม่เพื่อศึกษาพฤติกรรมของสัญญาณที่ถูกสร้างขึ้นด้วยข้อมูลและการตั้งค่าที่แตกต่างกัน

In [2]:
CARRIER_FREQ = 20   # ความถี่ของคลื่นพาหะ
BAUD = 10           # อัตราส่งสัญญาณ (ซิมโบลต่อวินาที)
DATA = '00011011'   # ข้อมูลดิจิทัลที่ต้องการส่ง
fig_options = dict(x_range=(-10,200))

## มอดูเลชันแบบ Binary Amplitude Shift Keying (ASK)
ASK ใช้ค่าแอมพลิจูดของคลื่นพาหะเป็นตัวบ่งชี้ค่าบิตข้อมูลทีละบิต

![วงจรมอดูเลชันแบบ ASK](pics/ask-circuit.png)

In [3]:
print("Baseband ASK signal (data bits = {})".format(DATA))
ask_linecoder = create_linecoder(BAUD,{'0':0.5,'1':1.0})
ask_baseband = ask_linecoder(DATA)
ask_baseband.plot_time_and_freq(ffig_options=fig_options)

print("Carrier signal")
ask_carrier = Signal(duration=ask_baseband.duration,func=lambda t:sin(2*pi*CARRIER_FREQ*t))
ask_carrier.plot_time_and_freq(ffig_options=fig_options)

print("Modulated signal")
ask_modulated = ask_baseband*ask_carrier
ask_modulated.plot_time_and_freq(ffig_options=fig_options)

Baseband ASK signal (data bits = 00011011)


Carrier signal


/home/ayumiizz/datacom/act6-analog/sigproc/sigproc.py:378: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ts.loc[interval,"a"] = func(ts[interval].t.as_matrix()-offset)


Modulated signal


## มอดูเลชันแบบ On-Off Keying (OOK)
OOK เป็นรูปแบบหนึ่งของ Binary ASK โดยที่ใช้แอมพลิจูดเท่ากับศูนย์แทนบิตข้อมูล 0 

In [4]:
print("Baseband OOK signal (data bits = {})".format(DATA))
ook_linecoder = create_linecoder(BAUD,{'0':0.0,'1':1.0})
ook_baseband = ook_linecoder(DATA)
ook_baseband.plot_time_and_freq(ffig_options=fig_options)

# print("Carrier signal")
ook_carrier = Signal(duration=ook_baseband.duration,func=lambda t:sin(2*pi*CARRIER_FREQ*t))
# ook_carrier.plot_time(ffig_options=fig_options)

print("Modulated signal")
ook_modulated = ook_baseband*ook_carrier
ook_modulated.plot_time_and_freq(ffig_options=fig_options)

Baseband OOK signal (data bits = 00011011)


Modulated signal


/home/ayumiizz/datacom/act6-analog/sigproc/sigproc.py:378: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ts.loc[interval,"a"] = func(ts[interval].t.as_matrix()-offset)


## มอดูเลชันแบบ Binary Phase Shift Keying (BPSK)
PSK ใช้ค่าเฟสของคลื่นพาหะเป็นตัวบ่งชี้ค่าบิตข้อมูล โดยใช้รูปแบบคลื่นที่มีเฟสแตกต่างกัน 2 รูปแบบ
![วงจรมอดูเลชันแบบ BPSK](pics/bpsk-circuit.png)

In [5]:
print("Baseband BPSK signal (data bits = {})".format(DATA))
bpsk_linecoder = create_linecoder(BAUD,{'0':-1.0,'1':1.0})
bpsk_baseband = bpsk_linecoder(DATA)
bpsk_baseband.plot_time_and_freq(ffig_options=fig_options)

print("Carrier signal")
bpsk_carrier = Signal(duration=bpsk_baseband.duration,func=lambda t:sin(2*pi*CARRIER_FREQ*t))
bpsk_carrier.plot_time_and_freq(ffig_options=fig_options)

print("Modulated signal")
bpsk_modulated = bpsk_baseband*bpsk_carrier
bpsk_modulated.plot_time_and_freq(ffig_options=fig_options)

Baseband BPSK signal (data bits = 00011011)


Carrier signal


/home/ayumiizz/datacom/act6-analog/sigproc/sigproc.py:378: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ts.loc[interval,"a"] = func(ts[interval].t.as_matrix()-offset)


Modulated signal


## มอดูเลชันแบบ Quadrature Phase Shift Keying (QPSK)
เป็น PSK แบบที่ใช้รูปแบบคลื่นที่เฟสแตกต่างกัน 4 รูปแบบ ทำให้ 1 รูปคลื่นแทนค่าข้อมูลได้ 2 บิต (2 bits/symbol) วงจรสร้างสัญญาณอย่างง่ายอาศัยการสร้างคลื่นซายน์ที่มีมุมแตกต่างกัน $90^\circ$ เพื่อนำมาผสมกันให้ได้รูปคลื่นที่มีเฟส 4 รูปแบบคือ $45^\circ$, $135^\circ$, $-45^\circ$ และ $-135^\circ$
![วงจรมอดูเลชันแบบ QPSK](pics/qpsk-circuit.png)

แยกข้อมูลออกเป็นสองสาย บิตในตำแหน่งคู่ และบิตในตำแหน่งคี่ พร้อมสร้าง line coder สำหรับสร้างสัญญาณดิจิทัลจากข้อมูลไบนารี

In [6]:
data1 = DATA[::2]   # เลือกเฉพาะบิตในตำแหน่งคู่
data2 = DATA[1::2]  # เลือกเฉพาะบิตในตำแหน่งคี่
print("Original data bits = {}".format(DATA))
print("Split into two parts: {} and {}".format(data1,data2))

qpsk_linecoder = create_linecoder(BAUD,{'0':-0.5,'1':0.5})

Original data bits = 00011011
Split into two parts: 0011 and 0101


สร้าง modulated signal สำหรับบิตในตำแหน่งคู่

In [7]:
print("Baseband signal for even-positioned bits ({})".format(data1))
qpsk_baseband1 = qpsk_linecoder(data1)
qpsk_baseband1.plot_time_and_freq(ffig_options=fig_options)

print("Carrier signal for even-positioned bits")
qpsk_carrier1 = Signal(duration=qpsk_baseband1.duration,func=lambda t:sin(2*pi*CARRIER_FREQ*t))
qpsk_carrier1.plot_time_and_freq(ffig_options=fig_options)

print("Modulated signal for even-positioned bits")
qpsk_modulated1 = qpsk_baseband1*qpsk_carrier1
qpsk_modulated1.plot_time_and_freq(ffig_options=fig_options)

Baseband signal for even-positioned bits (0011)


Carrier signal for even-positioned bits


/home/ayumiizz/datacom/act6-analog/sigproc/sigproc.py:378: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ts.loc[interval,"a"] = func(ts[interval].t.as_matrix()-offset)


Modulated signal for even-positioned bits


สร้าง modulated signal สำหรับบิตในตำแหน่งคู่ สังเกตว่า carrier signal มีเฟสนำหน้า carrier signal ของบิตคู่อยู่ $90^\circ$ (ใช้ฟังก์ชัน cosine)

In [8]:
print("Baseband signal for odd-positioned bits ({})".format(data2))
qpsk_baseband2 = qpsk_linecoder(data2)
qpsk_baseband2.plot_time_and_freq(ffig_options=fig_options)

print("Carrier signal for odd-positioned bits")
qpsk_carrier2 = Signal(duration=qpsk_baseband1.duration,func=lambda t:cos(2*pi*CARRIER_FREQ*t))
qpsk_carrier2.plot_time_and_freq(ffig_options=fig_options)

print("Modulated signal for odd-positioned bits")
qpsk_modulated2 = qpsk_baseband2*qpsk_carrier2
qpsk_modulated2.plot_time_and_freq(ffig_options=fig_options)

Baseband signal for odd-positioned bits (0101)


Carrier signal for odd-positioned bits


/home/ayumiizz/datacom/act6-analog/sigproc/sigproc.py:378: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ts.loc[interval,"a"] = func(ts[interval].t.as_matrix()-offset)


Modulated signal for odd-positioned bits


นำสองสัญญาณมาผสมกันเพื่อให้ได้เป็นสัญญาณลัพธ์

In [9]:
print("Original data bits: {}".format(DATA))
qpsk_modulated = qpsk_modulated1 + qpsk_modulated2
qpsk_modulated.plot_time_and_freq(ffig_options=fig_options)

Original data bits: 00011011


## ผลกระทบที่เกิดจากช่องสัญญาณแบบ band-pass
ทดลองนำเอาสัญญาณที่ผ่านกระบวนการ modulation ข้างต้นมาผ่าน band-pass filter เพื่อดูผลกระทบต่อตัวสัญญาณ

In [10]:
test_signal = bpsk_baseband

sig_tx = test_signal.copy()
sig_rx = test_signal.copy()

band = (CARRIER_FREQ-BAUD,CARRIER_FREQ+BAUD)
print("frequency band:",band)
sig_rx.filter(band)

fig = bkp.figure(height=300)
sig_tx.plot_time(fig=fig,line_options=dict(color="green",line_width=2))
sig_rx.plot_time(fig=fig,line_options=dict(color="red",line_width=1))
bkp.show(fig)

frequency band: (10, 30)
